In [1]:
import rp
import source.peekaboo as peekaboo
from source.peekaboo import run_peekaboo
from source.clip import get_clip_logits

[INFO] sd.py: loading stable diffusion...please make sure you have run `huggingface-cli login`.
Checkpoint path CompVis/stable-diffusion-v1-4


Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

You have disabled the safety checker for <class 'diffusers.pipelines.stable_diffusion.pipeline_stable_diffusion.StableDiffusionPipeline'> by passing `safety_checker=None`. Ensure that you abide to the conditions of the Stable Diffusion license and do not expose unfiltered results in services or applications open to the public. Both the diffusers team and Hugging Face strongly recommend to keep the safety filter enabled in all public facing circumstances, disabling it only for use-cases that involve analyzing network behavior or auditing its results. For more information, please have a look at https://github.com/huggingface/diffusers/pull/254 .


[INFO] sd.py: loaded stable diffusion!


In [ ]:
results=run_peekaboo(
                    'white tshirt',
                     "/home/ubuntu/Detic/detic_input/196.jpg",
                     "/home/ubuntu/Detic/detic_input/196.pt",
                     # "/home/ubuntu/Detic/detic_op/final_mask_rgb.png",
                     representation='detic', LEARNING_RATE= 0.05, #LEARNING_RATE=1e-04, 
                     GUIDANCE_SCALE=200, GRAVITY=0.05,
                     # GUIDANCE_SCALE=100, GRAVITY=.05,
                     min_step=200,
                     max_step=500,
                     NUM_ITER=500,
                    bilateral_kwargs={'iterations': 80, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}

                    #  bilateral_kwargs={'iterations': 300, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}
                     )

In [2]:
results=run_peekaboo(
                    'white tshirt',
                     "/home/ubuntu/Detic/detic_input/196.jpg",
                     "/home/ubuntu/Detic/detic_input/196.pt",
                     # "/home/ubuntu/Detic/detic_op/final_mask_rgb.png",
                     representation='detic', LEARNING_RATE= 0.05, #LEARNING_RATE=1e-04, 
                     GUIDANCE_SCALE=200, GRAVITY=0.05,
                     # GUIDANCE_SCALE=100, GRAVITY=.05,
                     min_step=200,
                     max_step=500,
                     NUM_ITER=400,
                    bilateral_kwargs={'iterations': 80, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}

                    #  bilateral_kwargs={'iterations': 300, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}
                     )

Once 
 
 Loop 
 
 Reflect

ic| Error: Failed to access the underlying source code for analysis. Was ic() invoked in a REPL (e.g. from the command line), a frozen application (e.g. packaged with PyInstaller), or did the underlying source code change during execution?


Saved results at peekaboo_results/white tshirt/023


In [ ]:
## 0s and 1s  -> Loss tries to reduce black patches to negative and maximizes white patches which have to get clamped
## 0s 

In [ ]:
!huggingface-cli whoami

In [ ]:
#Mario vs Luigi Part 1
results_collection=[]

In [ ]:
def get_clip_logits_per_image(prompt, images):
    return [get_clip_logits(image, [prompt])[0] for image in images]

def random_colors(length=100):
    return [rp.random_rgb_float_color() for _ in range(length)]

def get_score(foreground, alpha, prompt:str, colors:list):
    
    alpha=alpha>.5
    rp.display_image(rp.blend_images(rp.random_rgb_float_color(),rp.cv_resize_image(foreground,rp.get_image_dimensions(alpha)),alpha))
    alpha=rp.cv_dilate(alpha,5,circular=True)
    
    assert rp.is_image(foreground) and rp.is_image(alpha)
    images = [rp.blend_images(foreground, color, alpha) for color in colors]
    scores = get_clip_logits_per_image(prompt, images)
    score = rp.mean(scores)
    return score

In [ ]:
def ranked_results(results):
    colors = random_colors()
    def score(result):
        output = get_score(foreground = result.image,
                         alpha = result.alphas[0],
                         prompt = result.p_name,
                         colors = colors,
                        )
        print(output)
        return output
    scores = list(map(score,results))
    scores, results = rp.sync_sort(scores, results)
    
    #First is best
    scores, results = scores[::-1], results[::-1]
    
    return scores, results

def display_ranked_results(scores, results):
    for score, result in zip(scores, results):
        rp.display_image(
            rp.labeled_image(
                rp.horizontally_concatenated_images(
                    rp.cv_resize_image(result.image, (256, 256)), result.alphas[0]
                ),
                "%s : %f" % (result.p_name, score),
            )
        )

In [ ]:
results=run_peekaboo('Luigi',
                         "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                         representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, GRAVITY=.05,
                         min_step=200,
                         max_step=400,
                         NUM_ITER=100,
                         )

In [ ]:
from source.peekaboo import SimpleLabel

SimpleLabel('mario').name, SimpleLabel('mario').embedding

In [ ]:
name = 'Mario'

In [ ]:
label = SimpleLabel(name)
image=rp.load_image('https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg')
square_image_method='crop'

In [ ]:
image.shape

In [ ]:
image

In [ ]:
import rp
help(rp.is_image)

In [ ]:
from source.peekaboo import *
make_image_square(image,square_image_method)

In [ ]:
image=rp.as_rgb_image(rp.as_float_image(make_image_square(image,square_image_method)))

In [ ]:
image

In [ ]:
min_step=1
max_step=2
NUM_ITER=1

bilateral_kwargs=dict(kernel_size = 3,tolerance = .08,sigma = 5,iterations=40)
representation='raster bilateral'

In [ ]:
import pdb; pdb.set_trace()
PeekabooSegmenter(image,labels=[label],
                  name=name,bilateral_kwargs=bilateral_kwargs,
                  representation=representation, 
                  min_step=min_step, 
                  max_step=max_step,
                       ).to(device)

In [ ]:
display_ranked_results(*ranked_results(results_collection))

In [ ]:
import torch
import numpy as np
image_path = "/home/ubuntu/Detic/detic_input/6.jpg"
bb_path = "/home/ubuntu/Detic/detic_input/6.pt"
image = rp.load_image(image_path)
type(image)

In [ ]:



def get_alpha_mask(image, bb_path):
    bounding_boxes = torch.load(bb_path).detach().cpu()
    
    height, width = rp.get_image_dimensions(image)

    mask_tensor = torch.zeros((height, width))

    for box in bounding_boxes:
        x_min, y_min, x_max, y_max = map(int, box)
        mask_tensor[y_min:y_max, x_min:x_max] = 1

    return mask_tensor

def make_mask_square(alpha_mask: np.ndarray, method='crop'):
    height, width = rp.get_image_dimensions(alpha_mask)
    min_dim = min(height, width)
    max_dim = max(height, width)
    if method == 'crop':
        return make_mask_square(rp.crop_image(alpha_mask, min_dim, min_dim, origin='center'), 'scale')
    if method == 'scale':
        return torch.tensor(rp.resize_image(alpha_mask, (512, 512))).unsqueeze(0).repeat(3, 1, 1) #.unsqueeze(-1).expand((512, 512, 3))

alpha_mask = get_alpha_mask(image, bb_path)
# rp.display_image(alpha_mask)
# rp.display_image(make_mask_square(alpha_mask.numpy()))
# rp.get_image_dimensions(image)
# rp.get_image_dimensions(alpha_mask)
make_mask_square(alpha_mask.numpy()).shape
# alpha_mask.shape

In [ ]:
results=run_peekaboo(
                    'left most toilet',
                     "/home/ubuntu/Detic/detic_input/6.jpg",
                     "/home/ubuntu/Detic/detic_input/6.pt",
                     # "/home/ubuntu/Detic/detic_op/final_mask_rgb.png",
                     representation='fourier bilateral', LEARNING_RATE=1e-04, GUIDANCE_SCALE=100, GRAVITY=.05,
                     # GUIDANCE_SCALE=100, GRAVITY=.05,
                     min_step=200,
                     max_step=600,
                     NUM_ITER=300,
                     bilateral_kwargs={'iterations': 40, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}
                     )

In [ ]:
results=run_peekaboo(
                    'green bag on top left ',
                     "/home/ubuntu/refer/test_sm.jpg",
                     # "/home/ubuntu/Detic/detic_op/final_mask_rgb.png",
                     representation='fourier bilateral', LEARNING_RATE=1e-04, GUIDANCE_SCALE=100, GRAVITY=.05,
                     # GUIDANCE_SCALE=100, GRAVITY=.05,
                     min_step=200,
                     max_step=600,
                     NUM_ITER=300,
                     bilateral_kwargs={'iterations': 40, 'kernel_size': 3, 'sigma': 5, 'tolerance': 0.08}
                     )

In [ ]:
results_collection = []
for _ in range(10):
    results=run_peekaboo('apple logo on the laptop',
                         "/home/ubuntu/Detic/detic_op/laptop.png",
                         representation='raster bilateral', LEARNING_RATE=1e-01, GUIDANCE_SCALE=200, GRAVITY=.05,
                         min_step=200,
                         max_step=500,
                         NUM_ITER=200,
                         )
    results_collection.append(results)



In [ ]:
peekaboo.s.min_step=200
peekaboo.s.max_step=600

#Mario vs Luigi Part 1
results=run_peekaboo(
    # 'Luigi', #200/600
    # 'Princess Peach', #200/600H, 
    # 'Mario',
    # 'Bowser from super smash bros; yellow shell; seen from the front', #NO; stable diffusion is too weak to draw this - or I have bad prompts
    
    
                     # "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                     # "http://images6.fanpop.com/image/photos/43400000/Mario-Peach-super-mario-bros-43431011-644-704.png",
                                         
                     # bilateral_kwargs=dict(kernel_size = 3,
                     #                  tolerance = .08,
                     #                  sigma = 5,
                     #                  iterations=2,
                     #                 ),
                     # representation='raster',
    
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
#Mario vs Luigi Part 1
peekaboo.s.min_step, peekaboo.s.max_step=200,600
results=run_peekaboo('Mario',
                     "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=100,  GRAVITY=.05, min_step=200,
                         max_step=400,
                     )

In [ ]:
#Mario vs Luigi Part 2
results=run_peekaboo('Luigi',
                     "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                     )

In [ ]:
#Mario vs Luigi Part 2
label = peekaboo.SimpleLabel('Luigi')
blend_factor=.5
peekaboo.s.min_step, peekaboo.s.max_step=200,600
label.embedding = label.embedding*(1+blend_factor) - peekaboo.SimpleLabel('Mario').embedding*blend_factor
results=run_peekaboo('Luigi',
                     "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                     label=label,
                     min_step=200,
                     max_step=500,
                     NUM_ITER=150,
                     )

In [ ]:
#Mario vs Luigi Part 2
label = peekaboo.SimpleLabel('Luigi')
blend_factor=.5
# peekaboo.s.min_step, peekaboo.s.max_step=200,600

label.embedding = label.embedding*(1+blend_factor) - peekaboo.SimpleLabel('Mario').embedding*blend_factor
results=run_peekaboo('Luigi',
                     "https://i1.sndcdn.com/artworks-000160550668-iwxjgo-t500x500.jpg",
                     label=label,
                     min_step=200,
                     max_step=600,
                     NUM_ITER=100,
                     )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,400
#Wine and Cheese Part 1
results=run_peekaboo('Wine Glass half-full',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,600
#Wine and Cheese Part 1
results=run_peekaboo('Wine Glass half-full',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,400
#Wine and Cheese Part 2
results=run_peekaboo('Swiss Cheese',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,600
#Wine and Cheese Part 2
results=run_peekaboo('Swiss Cheese',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
# https://americasrestaurant.com/wp-content/uploads/2022/04/what-do-bread-and-butter-pickles-taste-like.jpg
peekaboo.s.min_step,peekaboo.s.max_step=200,600
#Wine and Cheese Part 3
results=run_peekaboo(
    # 'piano keyboard',
    # 'violin',
    'brass shiny saxophone on top',
                     "https://c8.alamy.com/comp/2GFDH27/violin-with-saxophone-and-piano-closeup-2GFDH27.jpg",
                     # representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
for _ in range(10):
    results=run_peekaboo(
        'Nemo Clownfish',
        'https://akns-images.eonline.com/eol_images/Entire_Site/2016917/rs_600x600-161017135949-600.finding-dory-2.101716.jpg',
        representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200,
        min_step=200, max_step=600,
        GRAVITY=.05,
        NUM_ITER=200,
    )
    results_collection.append(results)

In [ ]:
for _ in range(10):
    results=run_peekaboo(
        'brass shiny saxophone on top',
        "https://c8.alamy.com/comp/2GFDH27/violin-with-saxophone-and-piano-closeup-2GFDH27.jpg",
        representation='raster bilateral',
        LEARNING_RATE=1e-0,
        GUIDANCE_SCALE=200,
        min_step=200,
        max_step=900,
        GRAVITY=.05,
        NUM_ITER=200,
    )
    results_collection.append(results)

In [ ]:
run_peekaboo(
        'Nemo Clownfish',
        'https://akns-images.eonline.com/eol_images/Entire_Site/2016917/rs_600x600-161017135949-600.finding-dory-2.101716.jpg',
        representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200,
        min_step=200, max_step=600,
        GRAVITY=.05,
        NUM_ITER=200,
    )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,400
#Wine and Cheese Part 3
results=run_ipeekaboo('grapes',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
peekaboo.s.min_step,peekaboo.s.max_step=200,600
#Wine and Cheese Part 3
results=run_peekaboo('Green grapes',
                     "https://emeraldvalleyartisans.com/wp-content/uploads/2015/10/winecheese1.jpg",
                     representation='raster bilateral', LEARNING_RATE=1e-0, GUIDANCE_SCALE=200, NUM_ITER=500,  GRAVITY=.05,
                     )

In [ ]:
#Harry Potter Part 1
results=run_peekaboo('Harry Potter boy - daniel radcliffe - man with glasses',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     NUM_ITER=300
                    )

In [ ]:
#Harry Potter Part 2
label = peekaboo.SimpleLabel('Hermoine Granger')
blend_factor=.5
label.embedding = label.embedding*(1+blend_factor) - peekaboo.SimpleLabel('Harry Potter').embedding*blend_factor
results=run_peekaboo('Hermoine',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     label=label
                     )


In [ ]:
#Harry Potter Part 2
label = peekaboo.SimpleLabel('Hermoine Granger - Emma Watson - Girl with long hair')
blend_factor=.5
label.embedding = label.embedding*(1+blend_factor) - peekaboo.SimpleLabel('Harry Potter boy - daniel radcliffe - man with glasses').embedding*blend_factor

results=run_peekaboo('Hermoine',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     label=label
                     )

In [ ]:
#Emma Watson
#Good in a row: |||
#Bad prompts: "Hermoine Granger aka Emma Watson"
results=run_peekaboo('Hermoine Granger - Emma Watson - Girl with long hair',
                     "https://cometothedarkside97.files.wordpress.com/2021/05/images-2020-01-25t073939.551.jpeg?w=468",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Emma Watson
#Good in a row: 
#Bad prompts: 
results=run_peekaboo('Harry Potter boy - daniel radcliffe - man with glasses',
                     "https://prisiliaandayani.files.wordpress.com/2014/03/harry-ron-hermione-harry-potter-2422078-361-500.jpg",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Good in a row with fixed timestep 500: H,H,
#Bad prompts: 

# peekaboo.s.min_step=100
# peekaboo.s.max_step=500
for _ in range(10):
    results=run_peekaboo(
        'Harry Potter boy - daniel radcliffe - man with glasses',
        # 'Hermoine Granger - Emma Watson - Girl with long hair',

                         "https://i.guim.co.uk/img/media/380500f7fd9321a6cfd1bd1a3b3f104ad9797bb7/0_0_2000_1199/master/2000.jpg?width=1200&height=1200&quality=85&auto=format&fit=crop&s=f0d0ecb5a0c33aa91be270b08619e8d7",
                            # "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                         # "https://prisiliaandayani.files.wordpress.com/2014/03/harry-ron-hermione-harry-potter-2422078-361-500.jpg",

                         representation='raster bilateral',
                         # representation='raster',
                         # bilateral_kwargs=dict(kernel_size = 3,
                         #                  tolerance = .08,
                         #                  sigma = 5,
                         #                  iterations=2,
                         #                 ),
                         # representation='raster',
                         LEARNING_RATE=1e-0,
                         GUIDANCE_SCALE=200,
                         min_step=200,
                         max_step=400,
                         GRAVITY=.05,
                         NUM_ITER=200,
                         )
    results_collection.append(results)

In [ ]:
#Emma Watson
#Good in a row: ||X2X
#Good in a row with fixed timestep: |||||
#Bad prompts: 
results=run_peekaboo('Hermoine Granger - Emma Watson - Girl with long hair',
                     "https://i.guim.co.uk/img/media/380500f7fd9321a6cfd1bd1a3b3f104ad9797bb7/0_0_2000_1199/master/2000.jpg?width=1200&height=1200&quality=85&auto=format&fit=crop&s=f0d0ecb5a0c33aa91be270b08619e8d7",
                     representation='raster bilateral',
                     # bilateral_kwargs=dict(kernel_size = 3,
                     #                  tolerance = .08,
                     #                  sigma = 5,
                     #                  iterations=2,
                     #                 ),
                     # representation='raster',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Emma Watson
#Good in a row: |||
#Bad prompts: "Emma Watson"
results=run_peekaboo('Hermoine Granger aka Emma Watson',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Harry Potter 
#Good in a row: ||
results=run_peekaboo('Daniel radcliffe',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Harry Potter 
#Good in a row: |||||
results=run_peekaboo('Harry Potter boy - daniel radcliffe - man with glasses',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     )

In [ ]:
#Mario vs Luigi Part 1
#Good in a row: |||||
results=run_peekaboo('Hermoine Granger - Emma Watson - Girl with long hair',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     representation='raster bilateral',
                     LEARNING_RATE=1e-0,
                     GRAVITY=.05,
                     min_step=200,
                     max_step=500,
                     NUM_ITER=150,
                     )

In [ ]:
#Harry Potter Part 2
results=run_peekaboo('Hermoine Granger - Emma Watson - Girl with long hair - left',
                     "https://assets.teenvogue.com/photos/569e7d2a74da98670ff0ce1c/1:1/w_2159,h_2159,c_limit/MCDHAPO_EC797_H.JPG",
                     NUM_ITER=300
                    )

In [ ]:
#Stable Diffusion Basic Demo
#This is a demo cell showing how to simply use Stable Diffusion to generate an image. This is usefull for prompt engineering.
rp.display_image(peekaboo.s.prompt_to_img('Cake'))

In [ ]:
#Stable Diffusion Basic Demo
#This is a demo cell showing how to simply use Stable Diffusion to generate an image. This is usefull for prompt engineering.
for _ in range(30):
    rp.display_image(peekaboo.s.prompt_to_img('Bowser from super smash bros; yellow shell; seen from the front'))

In [ ]:
import torch
torch.cuda.is_available()